In [5]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import networkx as nx
from data_loader import load_track_data, load_race_data, transform_coordinates
from scipy.interpolate import interp1d
import matplotlib.pyplot as plt
import math
import geopandas as gpd
from shapely.geometry import Point
from shapely.geometry import LineString
import plotly.graph_objects as go


In [21]:
track_left_side, track_right_side = load_track_data(distance_pr_dot = 0)

# track_left_side = track_left_side[:1300]
# track_right_side = track_right_side[:1300]

track_left_side = transform_coordinates(track_left_side)
track_right_side = transform_coordinates(track_right_side)

track_left_side.reset_index(drop=True, inplace=True)
track_right_side.reset_index(drop=True, inplace=True)

gdf_left = gpd.GeoDataFrame(track_left_side, geometry=[Point(x, y) for x, y in zip(track_left_side["X-Coords"], track_left_side["Y-Coords"])])
gdf_right = gpd.GeoDataFrame(track_right_side, geometry=[Point(x, y) for x,y in zip(track_right_side["X-Coords"], track_right_side["Y-Coords"])])

gdf_left

c:\GitHub\RacingTrajectories\data_loader.py:82: ParserWarning:

Length of header or names does not match length of data. This leads to a loss of data with index_col=False.

c:\GitHub\RacingTrajectories\data_loader.py:83: ParserWarning:

Length of header or names does not match length of data. This leads to a loss of data with index_col=False.



index  Timestamp   Y-Coords   Z-Coords  X-Coords  Speed (Km/h)  \
0          0     12.072  50.335608  63.983009  6.947884      0.015407   
1          1     12.093  50.335608  63.983006  6.947884      0.015490   
2          2     12.108  50.335608  63.983006  6.947884      0.015375   
3          3     12.123  50.335608  63.983006  6.947884      0.015411   
4          4     12.141  50.335608  63.983002  6.947884      0.015397   
...      ...        ...        ...        ...       ...           ...   
27296  27296      2.571  50.335434  63.827377  6.947605      9.457843   
27297  27297      2.586  50.335434  63.827095  6.947605      8.855394   
27298  27298      2.604  50.335434  63.826775  6.947605      8.363351   
27299  27299      2.616  50.335434  63.826565  6.947604      7.880630   
27300  27300      2.634  50.335433  63.826267  6.947604      7.397411   

                       geometry  
0      POINT (6.94788 50.33561)  
1      POINT (6.94788 50.33561)  
2      POINT (6.94788 50.33561)  
3      POINT (6.94788 50.33561)  
4      POINT (6.94788 50.33561)  
...                         ...  
27296  POINT (6.94761 50.33543)  
27297  POINT (6.94760 50.33543)  
27298  POINT (6.94760 50.33543)  
27299  POINT (6.94760 50.33543)  
27300  POINT (6.94760 50.33543)  

[27301 rows x 7 columns]

In [25]:
# Create spatial indices for your GeoDataFrames. That will optimize spatial queries, like finding nearest neighbors:

sindex_left = gdf_left.sindex
sindex_right = gdf_right.sindex


In [36]:

nearest_points = []
max_spacing = 0.00002 #(1m or 10cm ?)

prev_left_point = gdf_left.geometry[0]
prev_right_point = gdf_right.geometry[0]
for idx,left_point in enumerate(gdf_left.geometry):
    possible_matches_index = list(sindex_right.nearest(left_point, 0))  # This should return indices of the nearest points

    if possible_matches_index:  # Making sure there is at least one match
        nearest_right_point_index = possible_matches_index[1]  # Take the first index if multiple are returned
        right_point = list(gdf_right.iloc[nearest_right_point_index].geometry)[0]  # Access the geometry of the nearest point
        
    if (prev_left_point.distance(left_point) > max_spacing) or (prev_right_point.distance(right_point) > max_spacing):

        nearest_points.append((left_point, right_point))
        prev_left_point = left_point
        prev_right_point = right_point


# Assuming nearest_points is a list of tuples containing Shapely Points
nearest_lines_gdf = gpd.GeoDataFrame(geometry=[LineString([p1, p2]) for p1, p2 in nearest_points if p2 is not None])

nearest_lines_gdf


geometry
0     LINESTRING (6.94788 50.33561, 6.94781 50.33573)
1     LINESTRING (6.94788 50.33561, 6.94779 50.33572)
2     LINESTRING (6.94787 50.33560, 6.94779 50.33571)
3     LINESTRING (6.94785 50.33559, 6.94777 50.33570)
4     LINESTRING (6.94783 50.33558, 6.94775 50.33569)
...                                               ...
2923  LINESTRING (6.94768 50.33548, 6.94761 50.33560)
2924  LINESTRING (6.94767 50.33547, 6.94759 50.33559)
2925  LINESTRING (6.94765 50.33546, 6.94758 50.33558)
2926  LINESTRING (6.94763 50.33545, 6.94756 50.33556)
2927  LINESTRING (6.94761 50.33544, 6.94754 50.33555)

[2928 rows x 1 columns]

In [37]:
import plotly.graph_objects as go

# Initialize a plotly figure
fig = go.Figure()

# Add left boundary to the figure
fig.add_trace(go.Scatter(
    x=gdf_left.geometry.x,
    y=gdf_left.geometry.y,
    mode='lines',
    name='Left Boundary',
    line=dict(color='blue')
))

# Add right boundary to the figure
fig.add_trace(go.Scatter(
    x=gdf_right.geometry.x,
    y=gdf_right.geometry.y,
    mode='lines',
    name='Right Boundary',
    line=dict(color='red')
))

# Add connections (nearest lines) to the figure
for line in nearest_lines_gdf.geometry:
    fig.add_trace(go.Scatter(
        x=[line.coords[0][0], line.coords[1][0]],
        y=[line.coords[0][1], line.coords[1][1]],
        mode='lines',
        name='Connection',
        line=dict(color='green', width=0.8)
    ))

# Set the plot layout
fig.update_layout(
    title='Track Boundaries and Nearest Connections',
    xaxis_title='X Coordinate',
    yaxis_title='Z Coordinate',
    showlegend=True,
    legend_title_text='Track Components',
    height=800,
)


default_zoom_x = [6.933, 6.951]  # Replace these with your desired x-axis range
default_zoom_y = [50.324, 50.338]  # Replace these with your desired y-axis range

# # Bottom Left
# default_zoom_x = [6.9339, 6.9357]  # Replace these with your desired x-axis range
# default_zoom_y = [50.3238, 50.3252]  # Replace 

# Top Right
# default_zoom_x = [6.9479, 6.951]  # Replace these with your desired x-axis range
# default_zoom_y = [50.3355, 50.338]  # Replace 

# Mid
default_zoom_x = [6.939, 6.942]  # Replace these with your desired x-axis range
default_zoom_y = [50.3315, 50.3338]  # Replace 

fig.update_xaxes(range=default_zoom_x)
fig.update_yaxes(range=default_zoom_y)

# Show the figure
fig.show()


In [10]:

def summarize_graph(G):
    # Basic information
    num_nodes = G.number_of_nodes()
    num_edges = G.number_of_edges()
    num_components = nx.number_connected_components(G)
    avg_degree = sum(dict(G.degree()).values()) / num_nodes
    
    # More detailed analysis
    components = [G.subgraph(c).copy() for c in nx.connected_components(G)]
    largest_component = max(components, key=len)
    diameter = nx.diameter(largest_component) if num_components == 1 else 'Undefined for disconnected graphs'
    density = nx.density(G)
    
    # Summary
    print(f'Number of Nodes: {num_nodes}')
    print(f'Number of Edges: {num_edges}')
    print(f'Number of Connected Components: {num_components}')
    print(f'Average Degree: {avg_degree:.2f}')
    print(f'Diameter of the Largest Component: {diameter}')
    print(f'Graph Density: {density:.4f}')


def create_left_right_pairs(df_left, df_right):
    pass

def is_point_within_track():
    pass


def create_track_network(df_left_reduced, df_right_reduced, grid_distance, diagonally_connected):
    
    # Interpolate boundaries
    left_spline_x, left_spline_y, right_spline_x, right_spline_y = create_cubic_splines(df_left_reduced, df_right_reduced)
    
    # Determine the vertical bounds of the track
    min_y = min(df_left_reduced['Y-Coords'].min(), df_right_reduced['Y-Coords'].min())
    max_y = max(df_left_reduced['Y-Coords'].max(), df_right_reduced['Y-Coords'].max())
    
    # Create the grid of nodes, checking if each is within track boundaries
    valid_nodes = []
    for y in np.arange(min_y, max_y, grid_distance):
        for x in np.arange(df_left_reduced['X-Coords'].min(), df_right_reduced['X-Coords'].max(), grid_distance):
            if REPLACE WITH FUNCTION TO CHECK IF POINT IS WITHIN TRACK:
                valid_nodes.append((x, y))

    # Create the network graph from the valid nodes
    G = nx.Graph()
    for node in valid_nodes:
        G.add_node(node)
    
    # Add edges based on grid_distance, include diagonals if specified
    directions = [(0, grid_distance), (grid_distance, 0)]
    if diagonally_connected:
        directions.extend([(grid_distance, grid_distance), (-grid_distance, grid_distance)])
    
    for node in valid_nodes:
        x, y = node
        for dx, dy in directions:
            neighbor = (x + dx, y + dy)
            if neighbor in valid_nodes:
                G.add_edge(node, neighbor)
    
    return G


G = create_track_network(track_left_side, track_right_side, grid_distance = 5, diagonally_connected= True)
summarize_graph(G)

SyntaxError: invalid syntax (398175548.py, line 43)

In [ ]:

def visualize_and_save_graph(G, file_name, dpi=300):
    # Set the size of the figure
    ax.set_aspect('equal')
    fig.set_size_inches(15, 15)
    plt.show()
    
    # Extract node positions from the graph G
    pos = {node: (node[0], node[1]) for node in G.nodes()}
    
    # Draw the network
    nx.draw(G, pos, node_size=10, width=1, with_labels=False, node_color='blue', edge_color='gray')
    
    plt.show()
    # Save the figure
    # plt.savefig(file_name, format='png', dpi=dpi, bbox_inches='tight')
    # plt.close()  # Close the figure to free memory

# Example usage:
visualize_and_save_graph(G, 'Data/Map_details/track_network.png', dpi=300)
